![header](../figures/logos_partenaires_DC_WOC-ESA.jpg)

# Mediterranean: Benchmark BFN-QG plot maps
 

***
**Authors:** Datlas <br>
**Copyright:** 2023 Datlas <br>
**License:** MIT

<div class="alert alert-block alert-success">
<h1><center>Mediterranean: Benchmark of BFN-QG plot maps</center></h1>
<h4><center> The notebook aims to plot maps produced by the BFN-QG system in the Mediterranean region. </center></h4> 
</div>

In [1]:
from glob import glob
import numpy as np
import os

In [2]:
import sys
sys.path.append('..')
from src.mod_plot import *
from src.mod_stat import *
from src.mod_spectral import *
from src.mod_interp import *
from src.mod_switchvar import *

In [3]:
import logging
logger = logging.getLogger()
logger.setLevel(logging.INFO)

<div class="alert alert-info" role="alert">

<h2>0. Parameters</h2>

</div>

In [4]:
time_min = '2019-01-15'                                        # time min for analysis
time_max = '2019-12-15'                                        # time max for analysis
output_dir = '../results'                                      # output directory path
os.system(f'mkdir -p {output_dir}')

# Region details
region = 'Mediterranean'
lon_min = -5                                          # domain min longitude
lon_max = 25                                          # domain max longitude
lat_min = 35.                                          # domain min latitude
lat_max = 47.                                          # domain max latitude

box_lonlat = {'lon_min':lon_min,'lon_max':lon_max,'lat_min':lat_min,'lat_max':lat_max}

method_name = 'BFNQG'



<div class="alert alert-info" role="alert">

<h2>1. Input files</h2>

</div>

## Sea Surface Height maps to evaluate

In [5]:
%%time
list_of_maps = sorted(glob('/Users/sammymetref/Documents/DATLAS/Notebooks/MASSH/mapping/myexamples/outputs/DC_WOC-Med_BFNQG/DC_WOC-Med_BFNQG_y2019m*'))
ds_maps = xr.open_mfdataset(list_of_maps, combine='nested', concat_dim='time')
ds_maps = ds_maps.sel(time=slice(time_min, time_max))
ds_maps = ds_maps.rename({'lon':'longitude','lat':'latitude'})
ds_maps.sla.attrs = {'grid_mapping': 'crs',
                     'long_name': 'Sea level anomaly',
                     'standard_name': 'sea_surface_height_above_sea_level',
                     'units': 'm'}
ds_maps

CPU times: user 4.14 s, sys: 495 ms, total: 4.64 s
Wall time: 7.99 s


<xarray.Dataset>
Dimensions:    (time: 335, latitude: 122, longitude: 301)
Coordinates:
  * time       (time) datetime64[ns] 2019-01-15 2019-01-16 ... 2019-12-15
  * longitude  (longitude) float64 -5.0 -4.9 -4.8 -4.7 ... 24.7 24.8 24.9 25.0
  * latitude   (latitude) float64 35.0 35.1 35.2 35.3 ... 46.8 46.9 47.0 47.1
Data variables:
    sla        (time, latitude, longitude) float64 dask.array<chunksize=(1, 122, 301), meta=np.ndarray>
    pv         (time, latitude, longitude) float64 dask.array<chunksize=(1, 122, 301), meta=np.ndarray>

In [6]:
ds_maps = sla_to_ssh(ds_maps,'/Users/sammymetref/Documents/DATLAS/Data/cnes_obs-sl_glo_phy-mdt_my_0.125deg_P20Y_1695393893725_1mdt.nc')

u,v = ssh_to_currents(ds_maps.ssh, ds_maps.longitude, ds_maps.latitude)

ds_maps = ds_maps.assign(ugos=lambda ds_maps: ds_maps.sla*0  + u)
ds_maps.ugos.attrs = {'grid_mapping': 'crs',
                    'long_name': 'Absolute geostrophic velocity: zonal component',
                    'standard_name': 'surface_geostrophic_eastward_sea_water_velocity',
                    'units': 'm/s'}

ds_maps = ds_maps.assign(vgos=lambda ds_maps: ds_maps.sla*0  + v)
ds_maps.vgos.attrs = {'grid_mapping': 'crs',
                    'long_name': 'Absolute geostrophic velocity: meridian component',
                    'standard_name': 'surface_geostrophic_northward_sea_water_velocity',
                    'units': 'm/s'}

## Plot DUACS geostrophic currents movie

In [8]:
movie(ds_maps,name_var='uv', method=method_name, region=region, dir_output='../results/',dim_name=['time','latitude','longitude'],
          framerate=24,Display=True,clim=[0,0.6],cmap='YlGnBu_r', newmovie=True)


## Compute and plot DUACS relative vorticity movie

In [9]:
rv = currents_to_relative_vorticity(np.array(ds_maps.ugos),np.array(ds_maps.vgos), ds_maps.longitude,ds_maps.latitude)

ds_maps = ds_maps.assign(rv=lambda ds_maps: ds_maps.sla * 0 + rv)

In [10]:
movie(ds_maps,name_var='rv', method=method_name, region=region, dir_output='../results/',dim_name=['time','latitude','longitude'],
          framerate=24,Display=True,clim=[-0.5,0.5],cmap='RdBu_r', newmovie=True)
